# install dependencies

In [ ]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [ ]:
%cd '/content/drive/MyDrive/Projects/CSE_583'

/content/drive/MyDrive/Projects/CSE_583


In [ ]:
!pip install ellipsis
!pip install h3pandas
!pip install -y h3-py
!pip install geojson
import h3


Usage:   
  pip3 install [options] <requirement specifier> [package-index-options] ...
  pip3 install [options] -r <requirements file> [package-index-options] ...
  pip3 install [options] [-e] <vcs project url> ...
  pip3 install [options] [-e] <local project path> ...
  pip3 install [options] <archive url/path> ...

no such option: -y


In [ ]:
!pip install mercantile
!pip install folium
!pip install rasterio
!pip install rasterstats

In [ ]:
import pandas as pd
import geopandas as gpd
import shapely.geometry
from shapely.geometry import Polygon
from geojson import Feature, Point, FeatureCollection
import json
import math
import mercantile
from tqdm import tqdm
from folium import GeoJson
import os
import tempfile
import fiona
import folium
import os
import requests
import rasterio
import rasterstats
import matplotlib
import matplotlib.pyplot as plt

In [ ]:
demo_data = gpd.read_file("https://minedbuildings.blob.core.windows.net/global-buildings/buildings-with-height-coverage.geojson")

In [ ]:
demo_data.loc[:1]
demo_sliced = demo_data.loc[60000:]
gdf = gpd.GeoDataFrame(demo_sliced, geometry='geometry')

# Use the centroid of all polygons to center the map
centroid = demo_sliced.geometry.centroid.unary_union.centroid
m = folium.Map(location=[centroid.y, centroid.x], zoom_start=12)

# Add the GeoDataFrame to the map
folium.GeoJson(demo_sliced).add_to(m)

# Show the map
m

<ipython-input-7-7755310fa034>:6: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = demo_sliced.geometry.centroid.unary_union.centroid


# 0: file management

In [ ]:
raw_folder = 'data/'
raw_building_fn = "example_building_footprint.geojson"
raw_extent_fn = "example_aoi_polygon.geojson"
raw_weather_fn = "example_weather.csv"
raw_terrain_fn = "example_dem.tif"

In [ ]:
raw_building_path = os.path.join(raw_folder, raw_building_fn)
raw_extent_path = os.path.join(raw_folder, raw_extent_fn)
raw_weather_path = os.path.join(raw_folder, raw_weather_fn)
raw_terrain_path = os.path.join(raw_folder, raw_terrain_fn)
print(raw_building_path)
print(raw_extent_path)
print(raw_weather_path)
print(raw_terrain_path)

data/example_building_footprint.geojson
data/example_aoi_polygon.geojson
data/example_weather.csv
data/example_dem.tif


# 1: Define our area of interest (AOI)

In [ ]:
test_coordinates = [

            [-122.298, 47.617],
            [-122.298, 47.616],
            [-122.297, 47.616],
            [-122.297, 47.617],
]

In [ ]:
coordinates = [
            # [-122.16484503187519, 47.69090474454916],
            # [-122.16484503187519, 47.6217555345674],
            # [-122.06529607517405, 47.6217555345674],
            # [-122.06529607517405, 47.69090474454916],
            # [-122.16484503187519, 47.69090474454916],

            # [-122.26484503187519, 47.75090474454916],
            # [-122.26484503187519, 47.6217555345674],
            # [-122.06529607517405, 47.6217555345674],
            # [-122.06529607517405, 47.75090474454916],

            [-122.3737459, 47.721192],
            [-122.3737459, 47.493953],
            [-122.162127, 47.493953],
            [-122.162127, 47.721192],

        ]
aoi_geom = {
    "coordinates": [
        coordinates
    ],
    "type": "Polygon",
}
aoi_shape = shapely.geometry.shape(aoi_geom)
minx, miny, maxx, maxy = aoi_shape.bounds



In [ ]:
# Create a Shapely polygon from the coordinates
aoi_polygon = Polygon(coordinates)
# Create a GeoDataFrame
aoi_gdf = gpd.GeoDataFrame(index=[0], crs='EPSG:4326', geometry=[aoi_polygon])

# # Save the GeoDataFrame as a GeoJSON file
aoi_gdf.to_file(raw_extent_path, driver='GeoJSON')

# center of AOI
center_lat = (miny + maxy) / 2
center_lon = (minx + maxx) / 2


m = folium.Map(location=[center_lat, center_lon],tiles="openstreetmap", zoom_start=10)
folium.GeoJson(data=aoi_gdf["geometry"]).add_to(m)
# folium.Polygon(
#     locations=aoi_geom['coordinates'][0],
#     color='blue',
#     fill=True,
#     stroke=True,
#     stroke_color='red',
#     fill_color='black',
#     fill_opacity=0.6
# ).add_to(m)

m

# 2: Determine which tiles intersect our AOI

In [ ]:
quad_keys = set()
for tile in list(mercantile.tiles(minx, miny, maxx, maxy, zooms=9)):
    quad_keys.add(int(mercantile.quadkey(tile)))
quad_keys = list(quad_keys)
print(f"The input area spans {len(quad_keys)} tiles: {quad_keys}")

The input area spans 4 tiles: [21230032, 21230021, 21230030, 21230023]


In [ ]:
df = pd.read_csv(
    "https://minedbuildings.blob.core.windows.net/global-buildings/dataset-links.csv"
)

# 3: download GeoJSON files that intersects the input geometry

In [ ]:
idx = 0
combined_rows = []
# new a temporary dir tmpdir
with tempfile.TemporaryDirectory() as tmpdir:
    # Download the GeoJSON files for each tile that intersects the input geometry
    tmp_fns = []
    for quad_key in tqdm(quad_keys):
      # find the row with matching quad_key
        rows = df[df["QuadKey"] == quad_key]
        # if do find a row, get the url, read as josn, comvert to geodataframe
        if rows.shape[0] == 1:
            url = rows.iloc[0]["Url"]

            df2 = pd.read_json(url, lines=True)
            df2["geometry"] = df2["geometry"].apply(shapely.geometry.shape)

            gdf = gpd.GeoDataFrame(df2, crs=4326)
            gdf['height'] = gdf['properties'].apply(lambda x: x.get('height'))
            gdf = gdf.drop(columns=['properties'])
            # create a file path for new new gdf with quad_key as filename, append to file list tmp_fns
            fn = os.path.join(tmpdir, f"{quad_key}.geojson")
            tmp_fns.append(fn)
            if not os.path.exists(fn):
                gdf.to_file(fn, driver="GeoJSON")
        elif rows.shape[0] > 1:
            raise ValueError(f"Multiple rows found for QuadKey: {quad_key}")
        else:
            raise ValueError(f"QuadKey not found in dataset: {quad_key}")

    # Merge the GeoJSON files into a single file
    for fn in tmp_fns:
        with fiona.open(fn, "r") as f:
            # read every row in a GeoJSON file
            for row in tqdm(f):
                row = dict(row)
                shape = shapely.geometry.shape(row["geometry"])
                # select shape that is contained in area of interest
                if aoi_shape.contains(shape):
                    properties = row["properties"]
                    # Remove the original 'id' if present
                    if "id" in properties:
                        del properties["id"]

                    # Extract the height value from properties, assuming it's already a direct value and not a dict
                    height = properties.get('height')  # This assumes that 'height' is directly stored in properties

                    # Create a new properties dictionary with only 'id' and 'height'
                    new_properties = {"id": idx, "height": height}

                    idx += 1

                    # Update the row with the new properties
                    row["properties"] = new_properties

                    # Append the updated row to the combined_rows list
                    combined_rows.append(row)

100%|██████████| 346621/346621 [01:17<00:00, 4447.31it/s]


In [ ]:
# 更新 schema 以包括 'height'
schema = {
    "geometry": "Polygon",
    "properties": {
        "id": "int",
        "height": "float"
    }
}

# 使用更新后的 schema 写入文件
with fiona.open(raw_building_path, "w", driver="GeoJSON", crs="EPSG:4326", schema=schema) as f:
    for row in combined_rows:
        # 确保每个 row 的属性都符合 schema，包括 'height' 字段
        properties = row['properties']
        new_properties = {
            'id': properties['id'],
            'height': properties.get('height') # 直接从原始 properties 字典获取 'height' 值
        }

        # 检查 'height' 值是否为 None，如果是，则可能需要处理（取决于您的需求）
        if new_properties['height'] is None:
            # 如果不希望包含 'height'，可以删除该键或设置默认值
            # del new_properties['height']
            # 或
            # new_properties['height'] = 0.0  # 或任何合适的默认值
            continue  # 或者如果不想写入没有高度的要素，则跳过

        # 构造新的行字典来匹配 schema
        new_row = {
            'type': 'Feature',
            'geometry': shapely.geometry.mapping(shapely.geometry.shape(row['geometry'])),
            'properties': new_properties
        }

        # 写入新的行
        f.write(new_row)

In [ ]:
raw_building = gpd.read_file(raw_building_path)
raw_building.head()

id    height                                           geometry
0   0  6.167338  POLYGON ((-122.16323 47.51119, -122.16322 47.5...
1   1  6.117427  POLYGON ((-122.16348 47.50285, -122.16367 47.5...
2   2  4.593605  POLYGON ((-122.16416 47.50349, -122.16446 47.5...
3   3  3.569735  POLYGON ((-122.16704 47.50321, -122.16705 47.5...
4   4  6.165513  POLYGON ((-122.16833 47.50363, -122.16817 47.5...

In [ ]:
# data['height'].unique()
raw_building = raw_building.sort_values(by='height')
print(raw_building.shape)
raw_building

(212316, 3)


id     height                                           geometry
55672    55672  -1.000000  POLYGON ((-122.35696 47.52587, -122.35696 47.5...
45540    45540  -1.000000  POLYGON ((-122.35507 47.71654, -122.35507 47.7...
124845  124845  -1.000000  POLYGON ((-122.22277 47.58204, -122.22263 47.5...
137124  137124  -1.000000  POLYGON ((-122.31791 47.56376, -122.31782 47.5...
99555    99555  -1.000000  POLYGON ((-122.34103 47.59379, -122.34111 47.5...
...        ...        ...                                                ...
159258  159258  35.076077  POLYGON ((-122.19435 47.61355, -122.19523 47.6...
71122    71122  35.264725  POLYGON ((-122.33040 47.60923, -122.32997 47.6...
201179  201179  35.527683  POLYGON ((-122.16766 47.57632, -122.16708 47.5...
139402  139402  35.889099  POLYGON ((-122.33512 47.60771, -122.33485 47.6...
130572  130572  37.249786  POLYGON ((-122.33587 47.60470, -122.33588 47.6...

[212316 rows x 3 columns]

In [ ]:
raw_building['centroid'] = raw_building.geometry.centroid
raw_building.head()

<ipython-input-89-0654a740864c>:1: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  raw_building['centroid'] = raw_building.geometry.centroid


id  height                                           geometry  \
55672    55672    -1.0  POLYGON ((-122.35696 47.52587, -122.35696 47.5...   
45540    45540    -1.0  POLYGON ((-122.35507 47.71654, -122.35507 47.7...   
124845  124845    -1.0  POLYGON ((-122.22277 47.58204, -122.22263 47.5...   
137124  137124    -1.0  POLYGON ((-122.31791 47.56376, -122.31782 47.5...   
99555    99555    -1.0  POLYGON ((-122.34103 47.59379, -122.34111 47.5...   

                           centroid  
55672   POINT (-122.35700 47.52590)  
45540   POINT (-122.35503 47.71651)  
124845  POINT (-122.22275 47.58215)  
137124  POINT (-122.31787 47.56378)  
99555   POINT (-122.34117 47.59372)

In [ ]:
raw_building.describe()

id         height
count  212316.000000  212316.000000
mean   106157.500000       5.257968
std     61290.494214       2.060497
min         0.000000      -1.000000
25%     53078.750000       4.364029
50%    106157.500000       5.271928
75%    159236.250000       6.061120
max    212315.000000      37.249786

In [ ]:
gdf = gpd.GeoDataFrame(raw_building, geometry='geometry')

# Use the centroid of all polygons to center the map
centroid = raw_building.geometry.centroid.unary_union.centroid
m = folium.Map(location=[centroid.y, centroid.x], zoom_start=12)

# Add the GeoDataFrame to the map
folium.GeoJson(raw_building).add_to(m)

# Show the map
m

<ipython-input-169-b665e6805f0c>:4: UserWarning: Geometry is in a geographic CRS. Results from 'centroid' are likely incorrect. Use 'GeoSeries.to_crs()' to re-project geometries to a projected CRS before this operation.

  centroid = data.geometry.centroid.unary_union.centroid


# 4: download and trim DEM from the same AOI

In [ ]:
# https://prd-tnm.s3.amazonaws.com/StagedProducts/Elevation/13/TIFF/historical/n48w123/USGS_13_n48w123_20230608.tif
coordinates

In [ ]:
from rasterstats import zonal_stats
from rasterio.enums import Resampling
from rasterio.features import geometry_window
from rasterio.windows import Window

# Define the coordinates of the area of interest (AOI)
coordinates = [
    [-122.3737459, 47.721192],
    [-122.3737459, 47.493953],
    [-122.162127, 47.493953],
    [-122.162127, 47.721192]
        ]

# Define the URL of the GeoTIFF file to download
url = "https://prd-tnm.s3.amazonaws.com/StagedProducts/Elevation/13/TIFF/historical/n48w123/USGS_13_n48w123_20230608.tif"

# saved path
raw_geotiff_path = '/content/example_raw_dem.tif'
trimmed_geotiff_path = '/content/example_dem.tif'

# Download the GeoTIFF file
response = requests.get(url)

# Save the downloaded file to a local path
with open(raw_geotiff_path, "wb") as f:
    f.write(response.content)

In [ ]:
src.meta

{'driver': 'GTiff',
 'dtype': 'float32',
 'nodata': -999999.0,
 'width': 10812,
 'height': 10812,
 'count': 1,
 'crs': CRS.from_epsg(4269),
 'transform': Affine(9.259259269220167e-05, 0.0, -123.00055555579371,
        0.0, -9.25925927753796e-05, 48.00055555659458)}

In [ ]:
out_transform

Affine(9.259259269220167e-05, 0.0, -122.3737962958602,
       0.0, -9.25925927753796e-05, 47.721203704191254)

In [ ]:
from rasterio.mask import mask

# Ensure the GeoDataFrame is in the same CRS as the GeoTIFF
with rasterio.open(raw_geotiff_path) as src:
    gdf = aoi_gdf.to_crs(src.crs.data)

    # Perform the crop
    out_image, out_transform = mask(dataset=src, shapes=gdf.geometry, crop=True)
    out_meta = src.meta.copy()
    out_meta.update({
        "driver": "GTiff",
        "height": out_image.shape[1],
        "width": out_image.shape[2],
        "transform": out_transform
    })

# Save the cropped image
with rasterio.open(trimmed_geotiff_path, "w", **out_meta) as dest:
    dest.write(out_image)

/usr/local/lib/python3.10/dist-packages/pyproj/crs/crs.py:141: FutureWarning: '+init=<authority>:<code>' syntax is deprecated. '<authority>:<code>' is the preferred initialization method. When making the change, be mindful of axis order changes: https://pyproj4.github.io/pyproj/stable/gotchas.html#axis-order-changes-in-proj-6
  in_crs_string = _prepare_from_proj_string(in_crs_string)


In [ ]:
# Perform zonal statistics on the cropped raster
stats = zonal_stats(gdf, trimmed_geotiff_path, stats="mean", nodata=-9999)

# Print the average elevation
for stat in stats:
    print(f"Average elevation: {stat['mean']} meters.")

Average elevation: 48.163258842349116 meters.


# 5: load geolocation of weather station, aggregate building and terrain to point

## sample on how to plot geolocation with hex

In [ ]:
test_data = pd.read_csv("http://freakonometrics.free.fr/popfr19752010.csv")
test_data = test_data[['com_nom', 'lat', 'long', 'pop_2001']]
test_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 36318 entries, 0 to 36317
Data columns (total 4 columns):
 #   Column    Non-Null Count  Dtype  
---  ------    --------------  -----  
 0   com_nom   36318 non-null  object 
 1   lat       36318 non-null  float64
 2   long      36318 non-null  float64
 3   pop_2001  36318 non-null  float64
dtypes: float64(3), object(1)
memory usage: 1.1+ MB


In [ ]:
hex_ids = test_data.apply(lambda row: h3.geo_to_h3(row.lat, row.long, resolution=6), axis = 1)
test_data = test_data.assign(hex_id=hex_ids.values)

In [ ]:
len(test_databyhexid['hex_id'].unique())

14393

In [ ]:
test_databyhexid = test_data.groupby("hex_id", as_index=False).agg({"pop_2001": "sum"})
test_databyhexid.columns = ["hex_id", "value"]

In [ ]:
def hexagons_dataframe_to_geojson(df_hex, file_output = None, column_name = "value"):
    """
    Produce the GeoJSON for a dataframe, constructing the geometry from the "hex_id" column
    and with a property matching the one in column_name
    """
    list_features = []

    for i,row in df_hex.iterrows():
        try:
            geometry_for_row = { "type" : "Polygon", "coordinates": [h3.h3_to_geo_boundary(h=row["hex_id"],geo_json=True)]}
            feature = Feature(geometry = geometry_for_row , id=row["hex_id"], properties = {column_name : row[column_name]})
            list_features.append(feature)
        except:
            print("An exception occurred for hex " + row["hex_id"])

    feat_collection = FeatureCollection(list_features)
    geojson_result = json.dumps(feat_collection)
    return geojson_result

def get_color(custom_cm, val, vmin, vmax):
    return matplotlib.colors.to_hex(custom_cm((val-vmin)/(vmax-vmin)))

def choropleth_map(df_aggreg, column_name = "value", border_color = 'black', fill_opacity = 0.7, color_map_name = "Blues", initial_map = None):
    """
    Creates choropleth maps given the aggregated data. initial_map can be an existing map to draw on top of.
    """
    #colormap
    min_value = df_aggreg[column_name].min()
    max_value = df_aggreg[column_name].max()
    mean_value = df_aggreg[column_name].mean()
    print(f"Colour column min value {min_value}, max value {max_value}, mean value {mean_value}")
    print(f"Hexagon cell count: {df_aggreg['hex_id'].nunique()}")

    # the name of the layer just needs to be unique, put something silly there for now:
    name_layer = "Choropleth " + str(df_aggreg)

    if initial_map is None:
        initial_map = folium.Map(location= [47, 4], zoom_start=5.5, tiles="cartodbpositron")

    #create geojson data from dataframe
    geojson_data = hexagons_dataframe_to_geojson(df_hex = df_aggreg, column_name = column_name)

    # color_map_name 'Blues' for now, many more at https://matplotlib.org/stable/tutorials/colors/colormaps.html to choose from!
    custom_cm = matplotlib.cm.get_cmap(color_map_name)

    folium.GeoJson(
        geojson_data,
        style_function=lambda feature: {
            'fillColor': get_color(custom_cm, feature['properties'][column_name], vmin=min_value, vmax=max_value),
            'color': border_color,
            'weight': 1,
            'fillOpacity': fill_opacity
        },
        name = name_layer
    ).add_to(initial_map)

    return initial_map

In [ ]:
hexmap = choropleth_map(df_aggreg = test_databyhexid, color_map_name = "Blues", column_name = "value")
hexmap

Colour column min value 3.80536973678392, max value 2159195.976967395, mean value 4125.754285734566
Hexagon cell count: 14393


<ipython-input-16-62039932efd1>:44: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed two minor releases later. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap(obj)`` instead.
  custom_cm = matplotlib.cm.get_cmap(color_map_name)


In [ ]:
m = folium.Map(location=[test_data['lat'].mean(), test_data['long'].mean()], zoom_start=12)
# folium.Marker(location=[47.6062, -122.3321], popup='Seattle').add_to(m)
# folium.CircleMarker(location=[47.6062, -122.3321], radius=50, color='red', fill=True).add_to(m)
for i in range(len(test_data) - 1):
    # try:
        folium.Marker(location=[test_data['lat'][i], test_data['long'][i]], popup=f'{test_data["Station Name"][i]}').add_to(m)
    # except KeyError:
    #     pass
m

## load weather data with geolocation

In [ ]:
raw_weather = pd.read_csv('data/weather_Seattle.csv')
print(raw_weather.shape)
# raw_weather = raw_weather.dropna(subset=['Ave temp annual_F'])
print(raw_weather.columns)
print(raw_weather.shape)
raw_weather.head()

(48, 7)
Index(['Station ID', 'Station Name', 'Lat', 'Lon', 'Elev (ft.)',
       'Ave temp annual_F', 'Note'],
      dtype='object')
(48, 7)


Station ID            Station Name     Lat      Lon  Elev (ft.)  \
0  KWASEATT2119       Belltown - Lenora  47.613 -122.342         194   
1  KWASEATT2336      Avalon LQA Seattle  47.620 -122.356         120   
2  KWASEATT2379     J'Oz 4 - The Veduta  47.621 -122.327         246   
3  KWASEATT2850  mrweather Capitol Hill  47.622 -122.318         335   
4  KWASEATT2696              Seattle CD  47.602 -122.312         253   

   Ave temp annual_F     Note  
0          50.107945      NaN  
1          53.560274      NaN  
2          52.952329      NaN  
3                NaN  no data  
4          53.064187      NaN

## create hexgon

In [ ]:
def create_hexagon(lat, lon, radius):
    # number of sides
    n_sides = 6
    # Convert latitude and longitude to radians
    lat_rad = math.radians(lat)
    lon_rad = math.radians(lon)
    # Earth's radius in meters
    earth_radius = 6371000

    # Calculate the radius of our hexagon in radians
    r_rad = radius / earth_radius

    # Calculate the vertices of the hexagon
    hexagon_vertices = []
    for i in range(n_sides):
        angle = math.pi / 3 * i
        x = lon_rad + r_rad * math.cos(angle)
        y = lat_rad + r_rad * math.sin(angle)
        # Convert the vertex back to degrees
        vertex = (math.degrees(x), math.degrees(y))
        hexagon_vertices.append(vertex)

    return Polygon(hexagon_vertices)

In [ ]:
raw_weather['hex'] = raw_weather.apply(lambda row: create_hexagon(row['Lat'], row['Lon'], 160), axis=1)
raw_weather.head()

Station ID            Station Name     Lat      Lon  Elev (ft.)  \
0  KWASEATT2119       Belltown - Lenora  47.613 -122.342         194   
1  KWASEATT2336      Avalon LQA Seattle  47.620 -122.356         120   
2  KWASEATT2379     J'Oz 4 - The Veduta  47.621 -122.327         246   
3  KWASEATT2850  mrweather Capitol Hill  47.622 -122.318         335   
4  KWASEATT2696              Seattle CD  47.602 -122.312         253   

   Ave temp annual_F     Note            h3_id           hex_id  \
0          50.107945      NaN  8628d542fffffff  8c28d542ca133ff   
1          53.560274      NaN  8628d542fffffff  8c28d542d1a63ff   
2          52.952329      NaN  8628d542fffffff  8c28d542c7a93ff   
3                NaN  no data  8628d542fffffff  8c28d542eb0c1ff   
4          53.064187      NaN  8628d5427ffffff  8c28d5421ba41ff   

                                                 hex  
0  POLYGON ((-122.34056108543052 47.613, -122.341...  
1  POLYGON ((-122.35456108543053 47.62, -122.3552...  
2  POLYGON ((-122.32556108543052 47.6210000000000...  
3  POLYGON ((-122.31656108543052 47.622, -122.317...  
4  POLYGON ((-122.31056108543052 47.602, -122.311...

In [ ]:
m = folium.Map(location=[raw_weather.iloc[0]['Lat'], raw_weather.iloc[0]['Lon']], zoom_start=15)

In [ ]:
def hex_to_geojson(hexagon):
    return GeoJson({
        "type": "Feature",
        "geometry": shapely.geometry.mapping(hexagon)
    })
for _, row in raw_weather.iterrows():
    geojson_hex = hex_to_geojson(row['hex'])
    geojson_hex.add_to(m)
    # Add the point
    folium.Marker(
        [row['Lat'], row['Lon']],
        popup=f'Lat: {row["Lat"]}, Lon: {row["Lon"]}'
    ).add_to(m)
m

In [ ]:
# prompt: draw hexgon for the points in raw_weather, i can specify radius

hex_ids = raw_weather.apply(lambda row: h3.geo_to_h3(row.Lat, row.Lon, resolution=12), axis = 1)
raw_weather = raw_weather.assign(hex_id=hex_ids.values)
print(len(raw_weather['hex_id'].unique()))
print(raw_weather['hex_id'].shape)
raw_weather.head()

47
(48,)


Station ID            Station Name     Lat      Lon  Elev (ft.)  \
0  KWASEATT2119       Belltown - Lenora  47.613 -122.342         194   
1  KWASEATT2336      Avalon LQA Seattle  47.620 -122.356         120   
2  KWASEATT2379     J'Oz 4 - The Veduta  47.621 -122.327         246   
3  KWASEATT2850  mrweather Capitol Hill  47.622 -122.318         335   
4  KWASEATT2696              Seattle CD  47.602 -122.312         253   

   Ave temp annual_F     Note            h3_id           hex_id  
0          50.107945      NaN  8628d542fffffff  8c28d542ca133ff  
1          53.560274      NaN  8628d542fffffff  8c28d542d1a63ff  
2          52.952329      NaN  8628d542fffffff  8c28d542c7a93ff  
3                NaN  no data  8628d542fffffff  8c28d542eb0c1ff  
4          53.064187      NaN  8628d5427ffffff  8c28d5421ba41ff

In [ ]:
hex_weather = raw_weather.groupby("hex_id", as_index=False).agg({"Ave temp annual_F": "sum"})
hex_weather.columns = ["hex_id", "value"]

In [ ]:
hexmap = choropleth_map(df_aggreg = hex_weather, color_map_name = "Blues", column_name = "value")
hexmap

Colour column min value 0.0, max value 106.12837466, mean value 33.76822042617021
Hexagon cell count: 47


<ipython-input-16-62039932efd1>:44: MatplotlibDeprecationWarning: The get_cmap function was deprecated in Matplotlib 3.7 and will be removed two minor releases later. Use ``matplotlib.colormaps[name]`` or ``matplotlib.colormaps.get_cmap(obj)`` instead.
  custom_cm = matplotlib.cm.get_cmap(color_map_name)


In [ ]:
# prompt: how to show the points from raw_weather in folium

m = folium.Map(location=[raw_weather['Lat'].mean(), raw_weather['Lon'].mean()], zoom_start=12)
# folium.Marker(location=[47.6062, -122.3321], popup='Seattle').add_to(m)
# folium.CircleMarker(location=[47.6062, -122.3321], radius=50, color='red', fill=True).add_to(m)
for i in range(len(raw_weather) - 1):
    try:
        folium.Marker(location=[raw_weather['Lat'][i], raw_weather['Lon'][i]], popup=f'{raw_weather["Station Name"][i]}').add_to(m)
    except KeyError:
        pass
m

## aggregate info to hexgon